# This example shows how to track through a FODO cell

In [1]:
%plot -f SVG

In [2]:
RF_Track;


RF-Track, version 2.3.0a2

Copyright (C) 2016-2024 CERN, Geneva, Switzerland. All rights reserved.

Author and contact:
 Andrea Latina <andrea.latina@cern.ch>
 BE-ABP Group
 CERN
 CH-1211 GENEVA 23
 SWITZERLAND

This software is distributed under a CERN proprietary software
license in the hope that it will be useful, but WITHOUT ANY WARRANTY;
not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.

See the COPYRIGHT and LICENSE files at the top-level directory of
the RF-Track download area: https://gitlab.cern.ch/rf-track/download

RF-Track was compiled with GSL-2.7.1 and fftw-3.3.8-sse2-avx



## Bunch parameters

In [3]:
%% Bunch parameters
mass = RF_Track.electronmass; % MeV/c^2
charge = -1; % single-particle charge, in units of e
population = 1*RF_Track.nC; % number of real particles per bunch
Pc = 5; % reference momentum, MeV/c
P_Q = Pc / charge; % MV/c, reference rigidity

## FODO cell parameters

In [4]:
%% FODO cell parameters
Lcell = 2; % m
Lquad = 0; % m
Ldrift = Lcell/2 - Lquad; % m

mu = 90; % deg
k1L = sind(mu/2) / (Lcell/4); % 1/m, integrated normalised strength

strength = k1L * P_Q; % MeV/m, quadrupole strength

In thin-lens approximation, the matrix for the complete FODO cell reads
$$
M = 
\left(
\begin{matrix}
1 - \frac{l_d^2}{2f^2} & 2l_d \left( 1 + \frac{l_d}{2f} \right) \\ 
 \frac{l_d^2}{4{f}^3} - \frac{l_d}{2f^2}  & 1 - \frac{l_d^2}{2f^2}\\
\end{matrix}
\right),
$$
where $l_d$ the distance between the centre of the two quadrupoles and $f = 1/\left(k_1 \cdot l_q\right)$ is the quadrupole focal length. The length of the cell is $L_\text{cell} = 2 l_d$.

The phase advance, $\mu$, is related to the transfer matrix by: 
$$
cos{\mu} = \frac{1}{2}\text{Trace}(M) = 1 - \frac{l_d^2}{2f^2}.
$$
Since
$$
\cos(\mu) = 1 - 2\sin^2{\frac{\mu}{2}},
$$
one can write:
$$
\sin{\frac{\mu}{2}} = \frac{L}{4f} = \frac{k_1\,l_q\,L_\text{cell}}{4}.
$$

## Let's define the elements

In [5]:
% Half a focusing quadrupole
Qf = Quadrupole(Lquad/2, strength/2);

% A full, defocusing, quadrupole
QD = Quadrupole(Lquad, -strength);

% The drift
Dr = Drift(Ldrift);
Dr.set_tt_nsteps(30); % transport table

# Let's define the FODO cell

In [6]:
FODO = Lattice ();
FODO.append (Qf);
FODO.append (Dr);
FODO.append (QD);
FODO.append (Dr);
FODO.append (Qf);

In [7]:
FODO.get_length()

ans = 2


In [8]:
FODO.size()

ans = 5


In [9]:
FODO{4}.get_length()

ans = 1


# ...and a bunch

In [ ]:
%% Define Twiss parameters
Twiss = Bunch6d_twiss();
Twiss.emitt_x = 0.001; % mm.mrad, normalized emittances
Twiss.emitt_y = 0.001; % mm.mrad
Twiss.alpha_x = 0.0;
Twiss.alpha_y = 0.0;
Twiss.beta_x = Lcell * (1 + sind(mu/2)) / sind(mu); % m
Twiss.beta_y = Lcell * (1 - sind(mu/2)) / sind(mu); % m

%% Create the bunch
B0 = Bunch6d(mass, population, charge, Pc, Twiss, 10000);

In [ ]:
Twiss.beta_x
Twiss.beta_y

# Then, we can perform tracking

In [ ]:
B1 = FODO.track(B0);

We can inquire the lattice to find out, for example, the Twiss parameters and the emittance

In [ ]:
T = FODO.get_transport_table('%S %beta_x %beta_y %emitt_x %emitt_y %sigma_x %sigma_y');

In [ ]:
hold on
plot(T(:,1), T(:,2), 'b-', 'linewidth', 2);
plot(T(:,1), T(:,3), 'r-', 'linewidth', 2);
legend({ '\beta_x', '\beta_y' });
xlabel('S [m]');
ylabel('\beta [m]');

In [ ]:
hold on
plot(T(:,1), T(:,4), 'b-', 'linewidth', 2);
plot(T(:,1), T(:,5), 'r-', 'linewidth', 2);
legend({ 'emitt_x', 'emitt_y' });
xlabel('S [m]');
ylabel('emitt [mm.mrad]');

In [ ]:
hold on
plot(T(:,1), T(:,6), 'b*-', 'linewidth', 2);
plot(T(:,1), T(:,7), 'r-', 'linewidth', 2);
legend({ 'sigma_x', 'sigma_y' });
xlabel('S [m]');
ylabel('sigma [mm]');

In [ ]:
M0 = B0.get_phase_space();
M1 = B1.get_phase_space();

In [ ]:
figure;
scatter(M0(:,1), M0(:,2))

In [ ]:
figure
scatter(M1(:,5), M1(:,6))
xlabel('t [mm/c]')
ylabel('P [MeV/c]')

figure
scatter(M1(:,5), M1(:,1))
xlabel('t [mm/c]')
ylabel('X [mm]')

In [ ]:
B1.get_phase_space('%Vz') (1:10)

In [ ]:
B0.get_phase_space('%m %Q %N')(1:10,:)